# Shallow detectors

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [ ]:
drivepath = '/content/gdrive/MyDrive/CMU/11785_Intro_to_Deep_Learning/DL_Group_Project/Dataset/Preprocessed_Data'

In [ ]:
!pip install tqdm

In [ ]:
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import os
from tqdm import tqdm
import time
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
import pandas as pd

In [ ]:
NUM_EPOCHS = 100
BATCH_SIZE = 64
HIDDEN_SIZE = 128
MODEL_VERSION = 1
LEARNING_RATE = 0.01
LOGISTIC_THRESHOLD = 0.5
OTHER_PHONEMES_PERCENT = 0.1

In [ ]:
cuda = torch.cuda.is_available()
num_workers = 8 if cuda else 0
DEVICE = "cuda" if cuda else "cpu"
print("Cuda = "+str(cuda)+" with num_workers = "+str(num_workers))

Cuda = True with num_workers = 8


In [ ]:
class PhonemeDataset(Dataset):
    
    def __init__(self, basepath, phoneme_tag, mode):
      # AA.wav
      # AA recording -> FRAMES, LABELS
      # 70% of FRAMES to train; 20% to dev; 10% to test
      # AA_train_features.npy (NUM_FRAMES, 40)
      # AA_dev_features.npy
      # AA_test_features.npy
      # AA_train_labels.npy

      # load specific recording features and labels
      phoneme_features_path = f"{basepath}/{phoneme_tag}_{mode}_features.npy"
      phoneme_labels_path = f"{basepath}/{phoneme_tag}_{mode}_labels.npy"

      phoneme_features = np.load(phoneme_features_path, allow_pickle=True)
      phoneme_labels = np.load(phoneme_labels_path, allow_pickle=True)

      print(f"[{phoneme_tag}] phoneme_features.shape: {phoneme_features.shape}")
      print(f"[{phoneme_tag}] phoneme_labels.shape: {phoneme_labels.shape}")

      phoneme_labels = np.where(phoneme_labels != 0, 1, 0)

      # load 40% of other_phoneme=1, do not load silence
      # go through all other files in basepath and load them with label=0
      with os.scandir(basepath) as entries:
        for entry in entries:
          if entry.is_file() and phoneme_tag not in entry.name:
            if "features" in entry.name and mode in entry.name:
              other_phoneme_tag = entry.name.split("_")[0]

              features_filepath = entry.path
              labels_filepath = f"{basepath}/{other_phoneme_tag}_{mode}_labels.npy"

              other_phoneme_features = np.load(features_filepath, allow_pickle=True)
              other_phoneme_labels = np.load(labels_filepath, allow_pickle=True)
              
              # find frames where label != 0
              non_zero_indexes = other_phoneme_labels.nonzero()
              non_zero_labels = other_phoneme_labels[non_zero_indexes]
              non_zero_features = other_phoneme_features[non_zero_indexes]
              end_frame = int(OTHER_PHONEMES_PERCENT * len(non_zero_labels)) + 1
              
              # stack to phoneme features
              phoneme_features = np.concatenate((phoneme_features, non_zero_features[:end_frame]))
              phoneme_labels = np.concatenate((phoneme_labels, np.zeros(non_zero_labels.shape)))
              

      self.X = phoneme_features
      self.Y = phoneme_labels

    def __len__(self):
        return len(self.X)
 
    # get a row at an index
    def __getitem__(self, index):
        x = torch.Tensor(self.X[index]).float()
        y = torch.as_tensor(self.Y[index]).float()
    
        return x,y

In [ ]:
class SilenceDataset(Dataset):
    
    def __init__(self, basepath, mode):
      phoneme_features = np.zeros((1, 40))  # eliminate this row
      phoneme_labels = np.zeros((1))  # eliminate this row

      # go through all other files in basepath and load phoneme=1 as label=0 
      # (non-silence) and phoneme=0 as label=1 (silence)
      with os.scandir(basepath) as entries:
        for entry in entries:
          if entry.is_file() and phoneme_tag not in entry.name:
            if "features" in entry.name and mode in entry.name:
              other_phoneme_tag = entry.name.split("_")[0]

              features_filepath = entry.path
              labels_filepath = f"{basepath}/{other_phoneme_tag}_{mode}_labels.npy"

              other_phoneme_features = np.load(features_filepath, allow_pickle=True)
              other_phoneme_labels = np.load(labels_filepath, allow_pickle=True)
              
              # find frames where label != 0
              zero_indexes = np.where(other_phoneme_labels == 0)
              non_zero_indexes = other_phoneme_labels.nonzero()

              other_phoneme_labels[zero_indexes] = 1  # label=1 (silence)
              other_phoneme_labels[non_zero_indexes] = 0  # label=0 (phoneme)
              
              # stack to phoneme features
              phoneme_features = np.concatenate((phoneme_features, other_phoneme_features))
              phoneme_labels = np.concatenate((phoneme_labels, other_phoneme_labels))
              
      self.X = phoneme_features[1:]
      self.Y = phoneme_labels[1:]

    def __len__(self):
        return len(self.X)
 
    # get a row at an index
    def __getitem__(self, index):
        x = torch.Tensor(self.X[index]).float()
        y = torch.as_tensor(self.Y[index]).float()
    
        return x,y

In [ ]:
def make_dataloader(dataset, train, batch_size):
  if train:
    shuffle = True
    drop_last = True
  else:
    shuffle = False
    drop_last = False
    
  loader = DataLoader(dataset=dataset, batch_size=batch_size,
                      drop_last=drop_last, shuffle=shuffle,
                      pin_memory=True, num_workers=8)
  
  return loader

In [ ]:
class PhonemeShallowDetector(nn.Module):
  
  def __init__(self, hidden_size, activation):
    super(PhonemeShallowDetector, self).__init__()
    
    self.linear_layer = nn.Linear(in_features=40, out_features=hidden_size)
    self.bn_layer = nn.BatchNorm1d(num_features=hidden_size)
    self.activation = activation
    self.output_layer = nn.Linear(in_features=hidden_size, out_features=1)
    self.sigmoid = nn.Sigmoid()
    seq_params = [
      self.linear_layer,
      self.bn_layer,
      self.activation,
      self.output_layer,
      self.sigmoid
    ]

    self.network = nn.Sequential(*seq_params)
    
  def forward(self, x):
    return self.network(x)

In [ ]:
class ShallowDetector():

  def __init__(self, phoneme_tag):
    self.phoneme_tag = phoneme_tag

    if phoneme_tag == 'SIL':
      train_data = SilenceDataset(basepath=drivepath, mode="train")
      self.train_loader = make_dataloader(dataset=train_data, train=True, batch_size=BATCH_SIZE)
      print(f"[{phoneme_tag}] train_data.shape: {train_data.X.shape}")

      dev_data = SilenceDataset(basepath=drivepath, mode="dev")
      self.dev_loader = make_dataloader(dataset=dev_data, train=False, batch_size=BATCH_SIZE)
      print(f"[{phoneme_tag}] dev_data.shape: {dev_data.X.shape}")
    else:
      train_data = PhonemeDataset(basepath=drivepath, phoneme_tag=phoneme_tag, mode="train")
      self.train_loader = make_dataloader(dataset=train_data, train=True, batch_size=BATCH_SIZE)
      print(f"[{phoneme_tag}] train_data.shape: {train_data.X.shape}")

      dev_data = PhonemeDataset(basepath=drivepath, phoneme_tag=phoneme_tag, mode="dev")
      self.dev_loader = make_dataloader(dataset=dev_data, train=False, batch_size=BATCH_SIZE)
      print(f"[{phoneme_tag}] dev_data.shape: {dev_data.X.shape}")

    self.model = PhonemeShallowDetector(hidden_size=HIDDEN_SIZE, 
                                        activation=nn.LeakyReLU()).to(DEVICE)
    self.criterion = nn.BCELoss()
    self.optimizer = torch.optim.SGD(self.model.parameters(), lr=LEARNING_RATE, momentum=0.9)
    self.scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(self.optimizer, 'min')

    self.train_loss_per_epoch = []
    self.train_acc_per_epoch = []
    self.dev_loss_per_epoch = []
    self.dev_acc_per_epoch = []
  
  def save_model(self, epoch):
    model_epoch_path = "{}/shallow_detectors/model_{}_{}_{}".format(drivepath, 
                                                                    self.phoneme_tag, 
                                                                    MODEL_VERSION, 
                                                                    epoch)
    torch.save({
        'model_state_dict': self.model.state_dict(),
        'optimizer_state_dict': self.optimizer.state_dict(),
        'scheduler_state_dict': self.scheduler.state_dict(),
    }, model_epoch_path)
    # print('saved model: {}'.format(model_epoch_path))

  def train(self, epochs):
    # Run training and track with wandb
    total_batches = len(self.train_loader) * epochs
    example_ct = 0  # number of examples seen
    batch_ct = 0

    for epoch in tqdm(range(epochs)):
        train_loss = 0.0
        start_time = time.time()
        total_predictions = 0
        correct_predictions = 0

        true_labels = []
        predictions = []
        for _, (features, targets) in enumerate(self.train_loader):
            batch_loss, outputs = self.train_batch(features, targets)
            train_loss += batch_loss

            example_ct += len(features)
            batch_ct += 1

            targets = targets.reshape(-1, 1)

            # check number of correct predictions
            output_classes = torch.where(outputs > LOGISTIC_THRESHOLD, 1, 0).detach().cpu() # convert to class labels
            total_predictions += len(output_classes)
            correct_predictions += torch.sum(targets == output_classes)

            true_labels += list(targets)
            predictions += list(output_classes)

        end_time = time.time()

        train_loss /= example_ct
        print(f"training loss: {train_loss}; time: {end_time - start_time}s")
        
        if (epoch + 1) % 10 == 0 or epoch == (epochs - 1):
          report = classification_report(true_labels, predictions, output_dict=True)
          df = pd.DataFrame(report).transpose()
          df.to_csv(f"{drivepath}/shallow_detectors/reports_train_{self.phoneme_tag}_{MODEL_VERSION}_{epoch + 1}.csv", index=False)

        print(classification_report(true_labels, predictions))
        print(confusion_matrix(true_labels, predictions))

        self.train_loss_per_epoch.append(train_loss)
        #self.train_acc_per_epoch.append(train_acc)

        # evaluate model with validation data
        dev_loss = self.evaluate_model(epoch)
        
        self.dev_loss_per_epoch.append(dev_loss)
        #self.dev_acc_per_epoch.append(dev_acc)

        # Step with the scheduler
        self.scheduler.step(dev_loss)
      
    # epoch completed, save model
    self.save_model(epoch)

  def train_batch(self, features, targets):
    features, targets = features.to(DEVICE), targets.to(DEVICE)
    targets = targets.reshape(-1, 1)

    self.optimizer.zero_grad()

    # Forward pass ➡
    outputs = self.model(features)
    loss = self.criterion(outputs, targets)  # compare with target outputs
    # Backward pass ⬅
    loss.backward()
    # Step with optimizer
    self.optimizer.step()

    return loss.item(), outputs

  def evaluate_model(self, epoch):

    with torch.no_grad():
      self.model.eval()

      running_loss = 0.0
      total_predictions = 0.0
      correct_predictions = 0.0

      true_labels = []
      predictions = []

      example_ct = 0
      start_time = time.time()
      for batch_idx, (features, targets) in enumerate(self.dev_loader):
        features = features.to(DEVICE)
        targets = targets.to(DEVICE)
        targets = targets.reshape(-1, 1)

        example_ct += len(features)

        outputs = self.model(features)
        outputs = outputs.to(DEVICE)

        # check number of correct predictions
        output_classes = torch.where(outputs > LOGISTIC_THRESHOLD, 1, 0)  # convert to class labels
        total_predictions += len(output_classes)
        correct_predictions += torch.sum(targets == output_classes)

        loss = self.criterion(outputs, targets).detach()
        running_loss += loss.item()

        true_labels += list(targets.detach().cpu())
        predictions += list(output_classes.detach().cpu())
      
      end_time = time.time()

      running_loss /= example_ct
      print(f"testing loss: {running_loss}; time: {end_time - start_time}s")

      if (epoch + 1) % 10 == 0:
        report = classification_report(true_labels, predictions, output_dict=True)
        df = pd.DataFrame(report).transpose()
        df.to_csv(f"{drivepath}/shallow_detectors/reports_dev_{self.phoneme_tag}_{MODEL_VERSION}_{epoch + 1}.csv", index=False)
  
      print(classification_report(true_labels, predictions))
      print(confusion_matrix(true_labels, predictions))
      return running_loss

## 2. Training shallow detectors (per phoneme + one for silence)

In [ ]:
%cd /content/gdrive/MyDrive/CMU/11785_Intro_to_Deep_Learning/DL_Group_Project/Dataset/Preprocessed_Data

/content/gdrive/.shortcut-targets-by-id/1-5qSMUCOdbNlj6D2Mas-EnlePRAw5fu5/11785_Intro_to_Deep_Learning/DL_Group_Project/Dataset/Preprocessed_Data


In [ ]:
from utilities import PHONEME_MAPPER

In [ ]:
%cd /

/


In [ ]:
print(PHONEME_MAPPER)

{0: 'SIL', 1: 'AE', 2: 'AH', 3: 'AW', 4: 'AY', 5: 'B', 6: 'BIT', 7: 'D', 8: 'DH', 9: 'EE', 10: 'FF', 11: 'G', 12: 'HH', 13: 'IH', 14: 'II', 15: 'J', 16: 'K', 17: 'LL', 18: 'MM', 19: 'NN', 20: 'OH', 21: 'OO', 22: 'OW', 23: 'OY', 24: 'P', 25: 'RR', 26: 'SH', 27: 'SS', 28: 'T', 29: 'TH', 30: 'UE', 31: 'UH', 32: 'VV', 33: 'WW', 34: 'YY', 35: 'ZZ'}


In [179]:
for phoneme_index, phoneme_tag in PHONEME_MAPPER.items():
  detector = ShallowDetector(phoneme_tag)
  detector.train(epochs=NUM_EPOCHS)


/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 4, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))















  0%|          | 0/100 [00:00<?, ?it/s]

[SIL] train_data.shape: (49976, 40)
[SIL] dev_data.shape: (10724, 40)
training loss: 0.004852886349470236; time: 2.8077359199523926s
              precision    recall  f1-score   support

         0.0       0.91      0.78      0.84     19865
         1.0       0.87      0.95      0.91     30055

    accuracy                           0.88     49920
   macro avg       0.89      0.87      0.87     49920
weighted avg       0.89      0.88      0.88     49920

[[15542  4323]
 [ 1498 28557]]
testing loss: 0.00711133619454293; time: 0.6623959541320801s
              precision    recall  f1-score   support

         0.0       0.90      0.69      0.78      4925
         1.0       0.78      0.94      0.85      5799

    accuracy                           0.82     10724
   macro avg       0.84      0.81      0.82     10724
weighted avg       0.84      0.82      0.82     10724


















  1%|          | 1/100 [00:05<08:42,  5.28s/it]

[[3399 1526]
 [ 367 5432]]
training loss: 0.0025993418723094064; time: 2.6749870777130127s
              precision    recall  f1-score   support

         0.0       0.92      0.76      0.83     19869
         1.0       0.86      0.95      0.90     30051

    accuracy                           0.88     49920
   macro avg       0.89      0.86      0.87     49920
weighted avg       0.88      0.88      0.87     49920

[[15046  4823]
 [ 1397 28654]]
testing loss: 0.006789814872567843; time: 0.6451416015625s
              precision    recall  f1-score   support

         0.0       0.85      0.77      0.81      4925
         1.0       0.82      0.89      0.85      5799

    accuracy                           0.83     10724
   macro avg       0.84      0.83      0.83     10724
weighted avg       0.83      0.83      0.83     10724


















  2%|▏         | 2/100 [00:10<08:32,  5.23s/it]

...

testing loss: 0.0036864066314912817; time: 1.8591713905334473s
              precision    recall  f1-score   support

         0.0       0.92      0.98      0.95       632
         1.0       0.90      0.67      0.77       163

    accuracy                           0.92       795
   macro avg       0.91      0.83      0.86       795
weighted avg       0.92      0.92      0.91       795

[[620  12]
 [ 53 110]]
training loss: 2.1947163258745785e-05; time: 2.0079288482666016s
              precision    recall  f1-score   support

         0.0       0.95      0.99      0.97      2656
         1.0       0.93      0.81      0.87       672

    accuracy                           0.95      3328
   macro avg       0.94      0.90      0.92      3328
weighted avg       0.95      0.95      0.95      3328

[[2618   38]
 [ 128  544]]

















 99%|█████████▉| 99/100 [06:27<00:03,  3.97s/it]

testing loss: 0.003686406311678624; time: 1.776763916015625s
              precision    recall  f1-score   support

         0.0       0.92      0.98      0.95       632
         1.0       0.90      0.67      0.77       163

    accuracy                           0.92       795
   macro avg       0.91      0.83      0.86       795
weighted avg       0.92      0.92      0.91       795

[[620  12]
 [ 53 110]]
training loss: 2.1747429273091256e-05; time: 2.0670528411865234s
              precision    recall  f1-score   support

         0.0       0.95      0.99      0.97      2654
         1.0       0.93      0.81      0.87       674

    accuracy                           0.95      3328
   macro avg       0.94      0.90      0.92      3328
weighted avg       0.95      0.95      0.95      3328

[[2616   38]
 [ 128  546]]

















100%|██████████| 100/100 [06:31<00:00,  3.92s/it]

testing loss: 0.00368640665960668; time: 1.8026843070983887s
              precision    recall  f1-score   support

         0.0       0.92      0.98      0.95       632
         1.0       0.90      0.67      0.77       163

    accuracy                           0.92       795
   macro avg       0.91      0.83      0.86       795
weighted avg       0.92      0.92      0.91       795

[[620  12]
 [ 53 110]]
